In [1]:
import intake

In [2]:
df = intake.open_csv('./data/bird_migration/{species}.csv').read()

## HvPlot
Now that our data are loaded in, we can use hvplot to look directly at the data.

In [3]:
import pandas as pd
import hvplot.pandas

In [4]:
df.hvplot.points('lon', 'lat', height=500)

:Points   [lon,lat]

In [5]:
df.hvplot.points('lon', 'lat', height=500, datashade=True)

:DynamicMap   []
   :RGB   [lon,lat]   (R,G,B,A)

In [6]:
df.hvplot.points('lon', 'lat', height=500, color='day', cmap='colorwheel', size=1)

:Points   [lon,lat]   (day)

## Grouping

In [7]:
p = df.hvplot.points('lon', 'lat', height=500, color='day', cmap='colorwheel', groupby='species')
p

:DynamicMap   [species]
   :Points   [lon,lat]   (day)

In [8]:
print(p)

:DynamicMap   [species]
   :Points   [lon,lat]   (day)


We can inspect just one bird in the same way that we would us a dictionary:

In [9]:
bird = 'Connecticut_Warbler'
p[bird]

:Points   [lon,lat]   (day)

Notice the gap between days 77 and 104. To clean up the data a little, we'll just do a linear interpolation between consecutive days.

In [10]:
def fill_day(v):
    next_year = v.assign(day=v.day + v.day.max())
    last_year = v.assign(day=v.day - v.day.max())
    surrounding_years = pd.concat([last_year, v, next_year])
    filled = surrounding_years.assign(
        lat=surrounding_years.lat.interpolate(), 
        lon=surrounding_years.lon.interpolate())
    this_year = filled[filled.day.isin(v.day)]
    return this_year

In [11]:
filled_days = pd.concat([fill_day(v) for k, v in df.groupby('species')])

Now let's check on that Connecticut Warbler again:

In [12]:
filled_days.hvplot.points('lon', 'lat', height=500, color='day', cmap='colorwheel', groupby='species').select(species=bird)

:Points   [lon,lat]   (day)

## Combining plots
Now lets look at where various birds spend their time: 

In [13]:
day_p = filled_days.hvplot.points('lon', 'lat', color='day', cmap='colorwheel', groupby='species')
lat_p = filled_days.hvplot.points('day', 'lat', color='lon', groupby='species').hist(dimension='lat') 
(day_p + lat_p).cols(1)

:Layout
   .DynamicMap.I    :DynamicMap   [species]
      :Points   [lon,lat]   (day)
   .AdjointLayout.I :AdjointLayout
      :DynamicMap   [species]
         :Points   [day,lat]   (lon)
      :DynamicMap   [species]
         :Histogram   [lat]   (lat_frequency)

In [14]:
print(p[bird])

:Points   [lon,lat]   (day)


[Next Section](./02_holoviews.ipynb#Holoviews)